In [ ]:
using Distributions

using JuMP
using CPLEX

In [ ]:
# Demand distribution
mu = [100.0, 200, 150, 170, 180, 170, 170]
sigma = [20.0, 50, 30, 50, 40, 30, 50]

# For each location, we discretize the levels into
# low, medium, high, using quantiles.
q = [
    quantile(Normal(mu[i], sigma[i]), [1/6, 3/6, 5/6])
    for i in 1:7
]

const d = vec(collect(Iterators.product(q...)));

In [ ]:
# q = []
# for i in q1
#     append!(q, [round.(Int,i)]) 
#     #println(typeof([round.(Int,i)]))
# end
#floor.(Int,q1)

In [ ]:
#d[1][2]

In [ ]:
#sum(r[1,1:7])

In [ ]:
# Number of locations
# Number of scenarios
const N = 7
const M = 3^7;

In [ ]:
# holding cost 
h = 1.0
# shortage cost
p = 4.0
# transshipment cost
c = 0.5;

In [ ]:
# Decision Variables
model = Model(CPLEX.Optimizer)
@variables(model, begin
        e[1:M,1:N] >= 0
        f[1:M,1:N] >= 0
        q[1:M,1:N] >= 0
        r[1:M,1:N] >= 0
        t[1:M,1:N,1:N] >= 0
        s[1:N] >= 0
    end);

In [ ]:
# Objective Function Data
@objective(model, Min, (sum(h*e[m,i] for m in 1:M for i in 1:N)
        +sum(c*t[m,i,j] for m in 1:M for i in 1:N for j in 1:N if i!=j)
    +sum(p*r[m,i] for m in 1:M for i in 1:N))/M)

0.0004572473708276177 e[1,1] + 0.0004572473708276177 e[1,2] + 0.0004572473708276177 e[1,3] + 0.0004572473708276177 e[1,4] + 0.0004572473708276177 e[1,5] + 0.0004572473708276177 e[1,6] + 0.0004572473708276177 e[1,7] + 0.0004572473708276177 e[2,1] + 0.0004572473708276177 e[2,2] + 0.0004572473708276177 e[2,3] + 0.0004572473708276177 e[2,4] + 0.0004572473708276177 e[2,5] + 0.0004572473708276177 e[2,6] + 0.0004572473708276177 e[2,7] + 0.0004572473708276177 e[3,1] + 0.0004572473708276177 e[3,2] + 0.0004572473708276177 e[3,3] + 0.0004572473708276177 e[3,4] + 0.0004572473708276177 e[3,5] + 0.0004572473708276177 e[3,6] + 0.0004572473708276177 e[3,7] + 0.0004572473708276177 e[4,1] + 0.0004572473708276177 e[4,2] + 0.0004572473708276177 e[4,3] + 0.0004572473708276177 e[4,4] + 0.0004572473708276177 e[4,5] + 0.0004572473708276177 e[4,6] + 0.0004572473708276177 e[4,7] + 0.0004572473708276177 e[5,1] + 0.0004572473708276177 e[5,2] + 0.0004572473708276177 e[5,3] + 0.0004572473708276177 e[5,4] + 0.000457

In [ ]:
@constraint(model, c1[m=1:M, i=1:N], f[m,i] 
    + sum(t[m,i,j] for j in 1:N if i!=j) + e[m,i] == s[i]);

In [ ]:
@constraint(model, c2[m=1:M, i=1:N], f[m,i] 
    + sum(t[m,j,i] for j in 1:N if i!=j) + r[m,i] == d[m][i]);

In [ ]:
@constraint(model, c3[m=1:M], sum(r[m,1:N])
    +sum(q[m,1:N])==sum(d[m]));

In [ ]:
@constraint(model, c4[m=1:M,i=1:N], e[m,i]+q[m,i]==s[i]);

In [ ]:
optimize!(model)

Version identifier: 22.1.0.0 | 2022-03-09 | 1a383f8ce
Parallel mode: deterministic, using up to 10 threads for concurrent optimization:
 * Starting dual Simplex on 1 thread...
 * Starting Barrier on 8 threads...
 * Starting primal Simplex on 1 thread...
Tried aggregator 1 time.
LP Presolve eliminated 0 rows and 15309 columns.
Reduced LP has 48114 rows, 153097 columns, and 336798 nonzeros.
Presolve time = 0.16 sec. (257.59 ticks)
Symmetry aggregator did 80191 additional substitutions.
Initializing dual steep norms . . .

Iteration log . . .
Iteration:     1   Dual objective     =             0.000000
Perturbation started.
Iteration:   101   Dual objective     =             0.000000
Iteration:  1026   Dual objective     =             0.135076
Iteration:  1954   Dual objective     =             0.256401
Iteration:  2885   Dual objective     =             0.367814
Iteration:  3819   Dual objective     =             0.471707
Iteration:  4381   Dual objective     =             0.524186
Itera

In [ ]:
@show objective_value(model)
@show value.(s)

objective_value(model) = 144.59568428318786
value.(s) = [107.25566174576274, 213.30204653389836, 158.46493870338983, 183.30204653389836, 190.88349261864414, 180.88349261864414, 183.3020465338984]


7-element Vector{Float64}:
 107.25566174576274
 213.30204653389836
 158.46493870338983
 183.30204653389836
 190.88349261864414
 180.88349261864414
 183.3020465338984